In this notebook I will plot all the longidutinal data for each individual separately

In [1]:
import data.breathe_data as br
import plotly.graph_objs as go
from plotly.subplots import make_subplots
import plotly.express as px
import data.helpers as dh
from datetime import timedelta
import o2_fev1_analysis.smooth as smooth
import pandas as pd
import numpy as np

In [2]:
# df = br.build_O2_FEV1_FEF2575_df(meas_file=2, remove_nan=False)
# df = br.load_meas_from_excel("BR_O2_FEV1_FEF2575_PEF_Nan")
df = br.load_meas_from_excel("BR_O2_FEV1_FEF2575_PEF_Nan_conservative_smoothing")
# df1 = br.load_meas_from_excel("BR_O2_FEV1_FEF2575_PEF_Nan_20240508")
# df2 = br.load_meas_from_excel("BR_O2_FEV1_FEF2575_PEF_Nan_20240410")
# df3 = br.load_meas_from_excel('BR_O2_FEV1_20240410')
# df = br.load_meas_from_excel("BR_O2_FEV1_FEF2575_PEF_inferred_AR_IA")

# Look at raw Breathe data

In [3]:
dfraw = pd.read_csv(
    dh.get_path_to_main()
    + f"DataFiles/BR/MeasurementData/Breathe_Spirometer_20231113.csv",
)

In [32]:
print(dfraw.shape)
dfraw.head(1)

(104324, 26)


UserId  EntityId  \
0  60d96f45-ec56-470b-89ae-0085c9f073a7   1000001   

                     Timestamp                     ClientTimestamp  IsDeleted  \
0  2022-08-04 17:15:31.3786092  2022-07-29 16:19:05.1254750 +00:00      False   

  CaptureType CaptureDeviceMake CaptureDeviceModel ThirdPartyId    PEF  ...  \
0   Bluetooth       Vitalograph   Lung Monitor BLE          NaN  326.0  ...   

   FEV1DivFVC  FEF2575  FEV1Percent  EVol  FVC  InvalidEntry  VolumeTimeCurve  \
0         NaN     2.53         88.0   NaN  NaN         False              NaN   

   FlowVolumeCurve  IsCapturePrimary                      CaptureSessionId  
0              NaN              True  00000000-0000-0000-0000-000000000000  

[1 rows x 26 columns]

In [39]:
dfraw = dfraw[~dfraw.IsDeleted]
dfraw = dfraw[~dfraw.InvalidEntry]
dfraw = dfraw[dfraw.PEF != 0]
print(dfraw.shape)
dfraw.head(1)

(60177, 26)


UserId  EntityId  \
0  60d96f45-ec56-470b-89ae-0085c9f073a7   1000001   

                     Timestamp                     ClientTimestamp  IsDeleted  \
0  2022-08-04 17:15:31.3786092  2022-07-29 16:19:05.1254750 +00:00      False   

  CaptureType CaptureDeviceMake CaptureDeviceModel ThirdPartyId    PEF  ...  \
0   Bluetooth       Vitalograph   Lung Monitor BLE          NaN  326.0  ...   

   FEV1DivFVC  FEF2575  FEV1Percent  EVol  FVC  InvalidEntry  VolumeTimeCurve  \
0         NaN     2.53         88.0   NaN  NaN         False              NaN   

   FlowVolumeCurve  IsCapturePrimary                      CaptureSessionId  
0              NaN              True  00000000-0000-0000-0000-000000000000  

[1 rows x 26 columns]

In [45]:
dfpat = br.load_patient_df_from_excel().drop(
    columns=["Age", "Sex", "Height", "StudyNumber"]
)
dfpat.head()

ID                          PartitionKey
0  101  bf306cf3-e0e3-4293-ae15-c4e8c2f85e34
1  102  6cb8bcf5-013f-47b0-8073-3b139e3fca7f
2  103  b8250d09-f356-410f-b2e6-6f1809760b96
3  104  e28915e3-e767-496b-b377-97b075891d48
4  105  2cdf6f89-78d4-439a-b7ab-ff18e191420b

In [48]:
dfraw = dfraw.merge(dfpat, right_on="PartitionKey", left_on="UserId")

In [57]:
print(sorted(dfraw[dfraw.PEF == 300].ID.unique()))

fig = px.histogram(dfraw, x="PEF", nbins=500, color="ID")
# fig = px.histogram(df1, x="FEF2575 % Predicted", nbins=500)
fig.update_layout(width=1500, height=700)
fig.show()

['104', '106', '107', '112', '116', '117', '122', '158', '162', '172', '176', '202', '203', '209', '220', '221', '224', '229', '230', '238', '239', '240', '252', '265', '272', '291', '292', '310', '319', '334', '339']


AttributeError: 'DataFrame' object has no attribute 'ID'

# Profile

In [ ]:
def plot_profile_for_ID_raw(df_for_ID):
    df_for_ID = df_for_ID.reset_index()
    fig = make_subplots(
        rows=4,
        cols=1,
        shared_xaxes=True,
        vertical_spacing=0.04,
    )
    fig.add_trace(
        go.Scatter(
            y=df_for_ID["O2 Saturation"], x=df_for_ID["Date Recorded"], mode="markers"
        ),
        row=1,
        col=1,
    )
    fig.add_trace(
        go.Scatter(y=df_for_ID.FEV1, x=df_for_ID["Date Recorded"], mode="markers"),
        row=2,
        col=1,
    )
    fig.add_trace(
        go.Scatter(
            y=df_for_ID.FEF2575,
            x=df_for_ID["Date Recorded"],
            mode="markers",
        ),
        row=3,
        col=1,
    )
    fig.add_trace(
        go.Scatter(
            y=df_for_ID.PEF,
            x=df_for_ID["Date Recorded"],
            mode="markers",
        ),
        row=4,
        col=1,
    )
    fig.update_yaxes(
        title="SpO2<br>(%)",
        row=1,
        col=1,
        range=[
            np.nanmin(df["O2 Saturation"]) * 0.98,
            np.nanmax(df["O2 Saturation"]) * 1.02,
        ],
    )
    fig.update_yaxes(
        title="FEV1<br>(L)",
        row=2,
        col=1,
        range=[np.nanmin(df.FEV1) * 0.98, np.nanmax(df.FEV1) * 1.02],
    )
    fig.update_yaxes(
        title="FEF2575<br>(L/s)",
        row=3,
        col=1,
        range=[np.nanmin(df.FEF2575) * 0.98, np.nanmax(df.FEF2575) * 1.02],
    )
    fig.update_yaxes(
        title="PEF<br>(L/min)",
        row=4,
        col=1,
        range=[np.nanmin(df.PEF) * 0.98, np.nanmax(df.PEF) * 1.02],
    )
    fig.update_yaxes(nticks=10)
    fig.update_traces(marker=dict(size=3))
    title = f"Measures for ID {df_for_ID.ID[0]}"
    fig.update_layout(
        font=dict(size=8), showlegend=False, title=title, height=1000, width=1400
    )
    fig.show()
    # fig.write_image(f"{dh.get_path_to_main()}PlotsBreathe/ID_profiles/{title}.pdf")
    return


df[df.ID == "405"].groupby(by="ID").apply(plot_profile_for_ID_raw)

### List IDs with PEF consistency issues
I will send those IDs to Magic Bullet for them to investigate on the issue's cause: device issue or data manipulation issue?

In [68]:
# ['104' '106' '107' '112' '116' '122' '158' '162' '176' '202' '220' '221'
#  '224' '229' '238' '265' '272' '310' '334']

for id in [
    "104",
    "106",
    "107",
    "112",
    "116",
    "122",
    "158",
    "162",
    "176",
    "202",
    "220",
    "221",
    "224",
    "229",
    "238",
    "265",
    "272",
    "310",
    "334",
]:
    print(id)
    dftmp = df[df.ID == id].dropna(subset="PEF")
    # dftmp = df[df.ID == '104'].dropna(subset='PEF')
    # dftmp = df[df.ID == '334'].dropna(subset='PEF')
    # dftmp = dftmp[dftmp.PEF < 500]
    fig = px.scatter(dftmp, x="Date Recorded", y="PEF")
    fig.update_traces(marker=dict(size=4))
    # fig.show()
    fig.write_image(
        dh.get_path_to_main() + f"PlotsBreathe/IDs with gap in PEF/{id}.pdf"
    )

# 1. ID that show this perfectly 104, 176, 202
# 2. ID that show it well 122, 224, 272, 334
# 3. ID that have huge issue: 238

104
106
107
112
116
122
158
162
176
202
220
221
224
229
238
265
272
310
334


# Profile with smoothing

In [12]:
same_range = False
raw_data_color = "black"

drug_df = br.load_drug_therapies()
df1 = df.copy()
df1["ecFEF2575%ecFEV1"] = df1["ecFEF2575"] / df1["ecFEV1"] * 100


def drug_therapy_color_dict():
    return {
        "Trikafta": "green",
        "Ivacaftor": "purple",
        "Symkevi": "purple",
        "Orkambi": "purple",
    }


def add_drug_therapy_shapes_for_ID(fig, df_for_ID, drug_df):
    # def add_drug_therapy_shapes_for_ID(fig, df_for_ID, drug_df):
    drug_df = drug_df[drug_df["DrugTherapyType"] != "Unknown"]
    drug_df_for_ID = drug_df[drug_df.ID == df_for_ID.ID[0]]
    shapes = []
    for _, row in drug_df_for_ID.iterrows():
        start_date = row.DrugTherapyStartDate
        stop_date = row.DrugTherapyStopDate
        if pd.isnull(stop_date):
            stop_date = df["Date Recorded"].max()

        for yref in ["y1", "y2", "y3", "y4", "y5"]:
            fig.add_shape(
                dict(
                    type="rect",
                    # xref="x",
                    yref=yref,
                    # yref="paper",
                    x0=start_date,
                    y0=0,
                    x1=stop_date,
                    y1=1000,
                    fillcolor=drug_therapy_color_dict()[row.DrugTherapyType],
                    opacity=0.08,
                    layer="below",
                    line_width=0,
                    name=row.DrugTherapyType,
                    # label=dict(text=row.DrugTherapyType, textposition="top center", font=dict(size=20)),
                )
            )
        # Add annotation
        fig.add_annotation(
            x=start_date,
            y=1.03,
            xref="x",
            yref="paper",
            # yref="y",
            text=row.DrugTherapyType,
            showarrow=False,
            font=dict(size=12),
        )
    return shapes


def plot_profile_for_ID(df_for_ID, df):
    df_for_ID = df_for_ID.reset_index()

    fig = make_subplots(
        rows=5,
        cols=1,
        shared_xaxes=True,
        vertical_spacing=0.01,
    )

    fig.add_trace(
        go.Scatter(
            y=df_for_ID["O2 Saturation"], x=df_for_ID["Date Recorded"], mode="markers"
        ),
        row=1,
        col=1,
    )
    fig.add_trace(
        go.Scatter(y=df_for_ID.FEV1, x=df_for_ID["Date Recorded"], mode="markers"),
        row=2,
        col=1,
    )
    fig.update_traces(marker=dict(color=raw_data_color), row=2, col=1)
    fig.add_trace(
        go.Scatter(y=df_for_ID.ecFEV1, x=df_for_ID["Date Recorded"], mode="markers"),
        row=2,
        col=1,
    )
    fig.add_trace(
        go.Scatter(
            y=df_for_ID.FEF2575,
            x=df_for_ID["Date Recorded"],
            mode="markers",
        ),
        row=3,
        col=1,
    )
    fig.update_traces(marker=dict(color=raw_data_color), row=3, col=1)
    fig.add_trace(
        go.Scatter(y=df_for_ID.ecFEF2575, x=df_for_ID["Date Recorded"], mode="markers"),
        row=3,
        col=1,
    )
    fig.add_trace(
        go.Scatter(
            y=df_for_ID["ecFEF2575%ecFEV1"],
            x=df_for_ID["Date Recorded"],
            mode="markers",
        ),
        row=4,
        col=1,
    )
    fig.add_trace(
        go.Scatter(
            y=df_for_ID["PEF (L/s)"],
            x=df_for_ID["Date Recorded"],
            mode="markers",
        ),
        row=5,
        col=1,
    )
    fig.update_traces(marker=dict(color=raw_data_color), row=5, col=1)
    fig.add_trace(
        go.Scatter(
            y=df_for_ID["ecPEF (L/s)"], x=df_for_ID["Date Recorded"], mode="markers"
        ),
        row=5,
        col=1,
    )
    fig.update_yaxes(
        title="SpO2<br>(%)",
        row=1,
        col=1,
        range=[
            np.nanmin(df["O2 Saturation"]) * 0.98,
            np.nanmax(df["O2 Saturation"]) * 1.02,
        ],
    )
    fig.update_yaxes(
        title="FEV1<br>(L)",
        row=2,
        col=1,
        range=[np.nanmin(df.FEV1) * 0.98, np.nanmax(df.FEV1) * 1.02],
    )
    fig.update_yaxes(
        title="FEF2575<br>(L/s)",
        row=3,
        col=1,
        range=[np.nanmin(df.FEF2575) * 0.98, np.nanmax(df.FEF2575) * 1.02],
    )
    fig.update_yaxes(
        title="ecFEF2575%ecFEV1",
        row=4,
        col=1,
        range=[
            np.nanmin(df["ecFEF2575%ecFEV1"]) * 0.98,
            max(200, np.nanmax(df_for_ID["ecFEF2575%ecFEV1"])) * 1.02,
        ],
    )
    fig.update_yaxes(
        title="PEF<br>(L/s)",
        row=5,
        col=1,
        range=[np.nanmin(df.PEF) / 60 * 0.98, np.nanmax(df.PEF) / 60 * 1.02],
    )
    fig.update_yaxes(nticks=10)
    fig.update_xaxes(
        mirror=True,
        ticks="outside",
        showline=True,
        linecolor="black",
        gridcolor="lightgrey",
    )
    fig.update_yaxes(
        mirror=True,
        ticks="outside",
        showline=True,
        linecolor="black",
        gridcolor="lightgrey",
    )
    fig.update_traces(marker=dict(size=4))
    title = f"Measures for ID {df_for_ID.ID[0]}, age {df_for_ID.Age[0]}y, height {df_for_ID.Height[0]}cm, {df_for_ID.Sex[0]}"
    fig.update_layout(
        font=dict(size=12),
        showlegend=False,
        title=title,
        height=1000,
        width=1400,
        plot_bgcolor="white",
    )
    add_drug_therapy_shapes_for_ID(fig, df_for_ID, drug_df),
    # fig.show()
    fig.write_image(
        f"{dh.get_path_to_main()}PlotsBreathe/ID_profiles/ID_profiles_with_conservative_smoothing/{title}.pdf"
    )
    return


df1[df1.ID == "201"].groupby(by="ID").apply(lambda df_for_ID: plot_profile_for_ID(df_for_ID, df1))
# df1.groupby(by="ID").apply(lambda df_for_ID: plot_profile_for_ID(df_for_ID, df1))

ERROR:root:ID 175 - ?? Symkevi start date is wrong, removing it because no clue about the true date (maybe 2019?)
ERROR:root:ID 206 - Updating Ivacaftor stop date to not overlap and changing Ivacaftor + Symkevi to Trikafta


Empty DataFrame
Columns: []
Index: []

In [11]:
ls '/Users/tristan.trebaol/Desktop/PhD/PlotsBreathe/ID_profiles/ID_profiles_with_conservative_smoothing/'

ls: /Users/tristan.trebaol/Desktop/PhD/PlotsBreathe/ID_profiles/ID_profiles_with_conservative_smoothing/: No such file or directory


# Smoothing benchmark

In [28]:
# IDs of interest for smoothing
# Rewrite
ids = ["101", "133", "201", "240"]  # "172", "198", "111",
# Examples of when feeding back smoothed measurements into the rolling window is a bad idea
# ids = 101, 111, 147

In [3]:
df_max_smooth = br.load_meas_from_excel("BR_O2_FEV1_FEF2575_PEF_Nan")
df_conservative = br.load_meas_from_excel(
    "BR_O2_FEV1_FEF2575_PEF_Nan_conservative_smoothing"
)

In [4]:
df_max_smooth.rename(
    {
        "ecFEV1": "ecFEV1 max rolling window",
        "ecFEF2575": "ecFEF2575 max rolling window",
        "ecPEF (L/s)": "ecPEF max rolling window",
    },
    axis=1,
    inplace=True,
)
df_conservative.rename(
    {
        "ecFEV1": "ecFEV1 conservative",
        "ecFEF2575": "ecFEF2575 conservative",
        "ecPEF (L/s)": "ecPEF conservative",
    },
    axis=1,
    inplace=True,
)
df_smooth = df_max_smooth.merge(
    df_conservative[
        [
            "ID",
            "Date Recorded",
            "ecFEV1 conservative",
            "ecFEF2575 conservative",
            "ecPEF conservative",
        ]
    ],
    on=["ID", "Date Recorded"],
)
df_smooth.shape

In [29]:
same_range = False
original_data_color = "black"

drug_df = br.load_drug_therapies()


def plot_profile_for_ID(df_for_ID, df, conservative):
    df_for_ID = df_for_ID.reset_index()

    fig = make_subplots(
        rows=3,
        cols=1,
        shared_xaxes=True,
        vertical_spacing=0.01,
    )

    fig.add_trace(
        go.Scatter(y=df_for_ID.FEV1, x=df_for_ID["Date Recorded"], mode="markers"),
        row=1,
        col=1,
    )
    fig.update_traces(marker=dict(color=original_data_color), row=1, col=1)
    if conservative:
        fig.add_trace(
            go.Scatter(
                y=df_for_ID["ecFEV1 conservative"],
                x=df_for_ID["Date Recorded"],
                mode="markers",
            ),
            row=1,
            col=1,
        )
    else:
        fig.add_trace(
            go.Scatter(
                y=df_for_ID["ecFEV1 max rolling window"],
                x=df_for_ID["Date Recorded"],
                mode="markers",
            ),
            row=1,
            col=1,
        )
    fig.add_trace(
        go.Scatter(
            y=df_for_ID.FEF2575,
            x=df_for_ID["Date Recorded"],
            mode="markers",
        ),
        row=2,
        col=1,
    )
    fig.update_traces(marker=dict(color=original_data_color), row=2, col=1)
    if conservative:
        fig.add_trace(
            go.Scatter(
                y=df_for_ID["ecFEF2575 conservative"],
                x=df_for_ID["Date Recorded"],
                mode="markers",
            ),
            row=2,
            col=1,
        )
    else:
        fig.add_trace(
            go.Scatter(
                y=df_for_ID["ecFEF2575 max rolling window"],
                x=df_for_ID["Date Recorded"],
                mode="markers",
            ),
            row=2,
            col=1,
        )
    fig.add_trace(
        go.Scatter(
            y=df_for_ID["PEF (L/s)"],
            x=df_for_ID["Date Recorded"],
            mode="markers",
        ),
        row=3,
        col=1,
    )
    fig.update_traces(marker=dict(color=original_data_color), row=3, col=1)
    if conservative:
        fig.add_trace(
            go.Scatter(
                y=df_for_ID["ecPEF conservative"],
                x=df_for_ID["Date Recorded"],
                mode="markers",
            ),
            row=3,
            col=1,
        )
    else:
        fig.add_trace(
            go.Scatter(
                y=df_for_ID["ecPEF max rolling window"],
                x=df_for_ID["Date Recorded"],
                mode="markers",
            ),
            row=3,
            col=1,
        )

    fig.update_yaxes(
        title="FEV1<br>(L)",
        row=1,
        col=1,
        range=[np.nanmin(df.FEV1) * 0.98, np.nanmax(df.FEV1) * 1.02],
    )
    fig.update_yaxes(
        title="FEF2575<br>(L/s)",
        row=2,
        col=1,
        range=[np.nanmin(df.FEF2575) * 0.98, np.nanmax(df.FEF2575) * 1.02],
    )
    fig.update_yaxes(
        title="PEF<br>(L/s)",
        row=3,
        col=1,
        range=[np.nanmin(df.PEF) / 60 * 0.98, np.nanmax(df.PEF) / 60 * 1.02],
    )
    fig.update_yaxes(nticks=10)
    fig.update_xaxes(
        mirror=True,
        ticks="outside",
        showline=True,
        linecolor="black",
        gridcolor="lightgrey",
    )
    fig.update_yaxes(
        mirror=True,
        ticks="outside",
        showline=True,
        linecolor="black",
        gridcolor="lightgrey",
    )
    fig.update_traces(marker=dict(size=4))
    title = f"Measures for ID {df_for_ID.ID[0]}, age {df_for_ID.Age[0]}y, height {df_for_ID.Height[0]}cm, {df_for_ID.Sex[0]}"
    fig.update_layout(
        font=dict(size=12),
        showlegend=False,
        title=title,
        height=700,
        width=1400,
        plot_bgcolor="white",
    )
    fig.show()
    # fig.write_image(
    #     f"{dh.get_path_to_main()}PlotsBreathe/ID profiles/Smoothing benchmark/{title}.pdf"
    # )
    return


# df_smooth[df_smooth.ID == "101"].groupby(by="ID").apply(
#     lambda df_for_ID: plot_profile_for_ID(df_for_ID, df1)
# )
df_smooth[df_smooth.ID.isin(ids)].groupby(by="ID").apply(
    lambda df_for_ID: plot_profile_for_ID(df_for_ID, df_smooth, conservative=False)
)
# df1.groupby(by="ID").apply(lambda df_for_ID: plot_profile_for_ID(df_for_ID, df1))

ERROR:root:ID 175 - ?? Symkevi start date is wrong, removing it because no clue about the true date (maybe 2019?)
ERROR:root:ID 206 - Updating Ivacaftor stop date to not overlap and changing Ivacaftor + Symkevi to Trikafta


Empty DataFrame
Columns: []
Index: []

In [14]:
df_max_smooth[df_max_smooth.ID == "101"]["PEF (L/s)"].max()

10.11666666666667

In [13]:
df[df.ID == "101"]["PEF (L/s)"].max()

10.11666666666667

# Smoothing exampls for ID 240

In [33]:
same_range = False
original_data_color = "black"

drug_df = br.load_drug_therapies()


def plot_profile_for_ID(df_for_ID, df, conservative):
    df_for_ID = df_for_ID.reset_index()

    fig = make_subplots(
        rows=2,
        cols=1,
        shared_xaxes=True,
        vertical_spacing=0.01,
    )

    fig.add_trace(
        go.Scatter(y=df_for_ID.FEV1, x=df_for_ID["Date Recorded"], mode="markers"),
        row=1,
        col=1,
    )
    fig.update_traces(marker=dict(color=original_data_color), row=1, col=1)
    if conservative:
        fig.add_trace(
            go.Scatter(
                y=df_for_ID["ecFEV1 conservative"],
                x=df_for_ID["Date Recorded"],
                mode="markers",
            ),
            row=1,
            col=1,
        )
    else:
        fig.add_trace(
            go.Scatter(
                y=df_for_ID["ecFEV1 max rolling window"],
                x=df_for_ID["Date Recorded"],
                mode="markers",
            ),
            row=1,
            col=1,
        )
    fig.add_trace(
        go.Scatter(
            y=df_for_ID.FEF2575,
            x=df_for_ID["Date Recorded"],
            mode="markers",
        ),
        row=2,
        col=1,
    )
    fig.update_traces(marker=dict(color=original_data_color), row=2, col=1)
    if conservative:
        fig.add_trace(
            go.Scatter(
                y=df_for_ID["ecFEF2575 conservative"],
                x=df_for_ID["Date Recorded"],
                mode="markers",
            ),
            row=2,
            col=1,
        )
    else:
        fig.add_trace(
            go.Scatter(
                y=df_for_ID["ecFEF2575 max rolling window"],
                x=df_for_ID["Date Recorded"],
                mode="markers",
            ),
            row=2,
            col=1,
        )

    fig.update_yaxes(
        title="FEV1<br>(L)",
        row=1,
        col=1,
        # range=[np.nanmin(df.FEV1) * 0.98, np.nanmax(df.FEV1) * 1.02],
    )
    fig.update_yaxes(
        title="FEF2575<br>(L/s)",
        row=2,
        col=1,
        # range=[np.nanmin(df.FEF2575) * 0.98, np.nanmax(df.FEF2575) * 1.02],
    )
    fig.update_yaxes(nticks=10)
    fig.update_xaxes(
        mirror=True,
        ticks="outside",
        showline=True,
        linecolor="black",
        gridcolor="lightgrey",
    )
    fig.update_yaxes(
        mirror=True,
        ticks="outside",
        showline=True,
        linecolor="black",
        gridcolor="lightgrey",
    )
    fig.update_traces(marker=dict(size=4))
    title = f"Measures for ID {df_for_ID.ID[0]}, age {df_for_ID.Age[0]}y, height {df_for_ID.Height[0]}cm, {df_for_ID.Sex[0]}"
    fig.update_layout(
        font=dict(size=12),
        showlegend=False,
        title=title,
        height=500,
        width=1400,
        plot_bgcolor="white",
    )
    fig.show()
    # fig.write_image(
    #     f"{dh.get_path_to_main()}PlotsBreathe/ID profiles/Smoothing benchmark/{title}.pdf"
    # )
    return


df_smooth[df_smooth.ID == "240"].groupby(by="ID").apply(
    lambda df_for_ID: plot_profile_for_ID(df_for_ID, df_smooth, conservative=True)
)
# df_smooth[df_smooth.ID.isin(ids)].groupby(by="ID").apply(lambda df_for_ID: plot_profile_for_ID(df_for_ID, df_smooth, conservative=False))
# df1.groupby(by="ID").apply(lambda df_for_ID: plot_profile_for_ID(df_for_ID, df1))

ERROR:root:ID 175 - ?? Symkevi start date is wrong, removing it because no clue about the true date (maybe 2019?)
ERROR:root:ID 206 - Updating Ivacaftor stop date to not overlap and changing Ivacaftor + Symkevi to Trikafta


Empty DataFrame
Columns: []
Index: []